In [ ]:
%matplotlib qt

import matplotlib.pyplot as plt
from data.tools import zplot as zp
import numpy as np

from vis.robot_dynamics import utils
from carmaker import utils as cm_utils

# Vehicle Data

In [ ]:
uri = 'chum://20200528T192032-vh6a_13@1590695284.92+20s' # North bound (0% grade, 20 kph tail wind, 6.6 Step ON, 2.54s coast)
# uri = 'chum://20200528T192032-vh6a_13@1590695222.68+20s' # South bound (1.5% uphill grade, 20 kph head wind, 7.14 Step ON, 2.62s coast)
topics = [
    '/planner/hero_state',
    '/vehicle/measurements',
    '/emu/debug',
    '/pseudo_planner/control',
    '/oxts/debug'
]

data = utils.load_data(uri, topics)

# CarMaker Data

In [ ]:
erg_file = '/home/dbelo/driving/carmaker/SimOutput/1576-desktop/20200601/longitudinal_control_step_torque_input_194318.erg' # North bound
# erg_file = '/home/dbelo/driving/carmaker/SimOutput/1576-desktop/20200601/longitudinal_control_step_torque_input_194628.erg' # South bound
erg = cm_utils.erg.load(erg_file)

# Correlation Plots

In [ ]:
# Simulation time offset
t0_sim = 18.73

# Wheel circumference as per Bosch BL4: 2.38m, BL5: 2.36
k_radps_to_kph_bl4 = 2.38/2/np.pi
k_radps_to_kph_bl5 = 2.36/2/np.pi

# Motor Torque
t0 = data['/pseudo_planner/control'].META.message_time_ns[0]/1e9
plt0 = zp.figure('Motor Torque', legend=True)
plt0.set_title('Motor Torque')
plt0.plot(
    data['/pseudo_planner/control'].META.message_time_ns/1e9 - t0,
    data['/pseudo_planner/control'].torque_system*0.5,
    'k',
    name='cmd front')
plt0.plot(
    data['/emu/debug'].META.message_time_ns/1e9 - t0,
    data['/emu/debug'].motor_front.torque,
    'm',
    name='front')
plt0.plot(
    data['/emu/debug'].META.message_time_ns/1e9 - t0,
    data['/emu/debug'].motor_front.torque,
    'b',
    name='rear')
plt0.plot(
    erg.data['Time'] - t0_sim,
    erg.data['m_edu_cmd_north'],
    'k--',    
    name='cmd front (sim)')
plt0.plot(
    erg.data['Time'] - t0_sim,
    erg.data['PT.Motor.Trq']*11.8,
    'm--',
    name='front (sim)')
plt0.plot(
    erg.data['Time'] - t0_sim,
    erg.data['PT.Motor1.Trq']*11.8,
    'm--',
    name='rear (sim)')
plt0.x_axis.set_label('Time', units='s')
plt0.x_axis.enable_grid(True)
plt0.y_axis.set_label('Motor Torque', units='Nm')
plt0.y_axis.enable_grid(True)

# Velocity
t0 = data['/vehicle/measurements'].META.message_time_ns[0]/1e9
plt1 = zp.figure('Vehicle Velocity', legend=True)
plt1.set_title('Vehicle Velocity')
plt1.plot(
    data['/vehicle/measurements'].META.message_time_ns/1e9 - t0,
    data['/vehicle/measurements'].dynamics.wheel_speeds.ne*k_radps_to_kph_bl5/k_radps_to_kph_bl4,
    'k',
    name='wheel speed q1')
plt1.plot(
    data['/vehicle/measurements'].META.message_time_ns/1e9 - t0,
    data['/vehicle/measurements'].dynamics.wheel_speeds.sw*k_radps_to_kph_bl5/k_radps_to_kph_bl4,
    'm',
    name='wheel speed q4')
plt1.plot(
    data['/oxts/debug'].META.message_time_ns/1e9 - t0,
    data['/oxts/debug'].raw_data.speed,
    'r',
    name='oxts speed')
plt1.plot(
    erg.data['Time'] - t0_sim,
    erg.data['Car.WheelSpd_FL']*k_radps_to_kph_bl5,
    'k--',
    name='wheel speed q1 (sim)')
plt1.plot(
    erg.data['Time'] - t0_sim,
    erg.data['Car.WheelSpd_RR']*k_radps_to_kph_bl5,
    'm--',
    name='wheel speed q4 (sim)')
plt1.plot(
    erg.data['Time'] - t0_sim,
    erg.data['Car.vx'],
    'r--',
    name='speed (sim)')
plt1.x_axis.link_to(plt0.x_axis)
plt1.x_axis.set_label('Time', units='s')
plt1.x_axis.enable_grid(True)
plt1.y_axis.set_label('Speed', units='m/s')
plt1.y_axis.enable_grid(True)

# Motor Velocity
plt2 = zp.figure('Motor Speed', legend=True)
plt2.set_title('Motor Speed')
plt2.plot(
    data['/emu/debug'].META.message_time_ns/1e9 - t0,
    data['/emu/debug'].motor_front.velocity_raw,
    'k',
    name='front motor velocity')
plt2.plot(
    erg.data['Time'] - t0_sim,
    erg.data['PT.Motor.rotv']*0.0315,
    'k--',
    name='front (sim)')
plt2.x_axis.link_to(plt1.x_axis)
plt2.x_axis.set_label('Time', units='s')
plt2.x_axis.enable_grid(True)
plt2.y_axis.set_label('Speed', units='m/s')
plt2.y_axis.enable_grid(True)

# Longitudinal Accel
plt3 = zp.figure('Longitudinal Accel', legend=True)
plt3.set_title('Longitudinal Accel')
plt3.plot(
    data['/planner/hero_state'].META.message_time_ns/1e9 - t0,
    data['/planner/hero_state'].body_acceleration.a_x,
    'k',
    name='long accel')
plt3.plot(
    erg.data['Time'] - t0_sim,
    erg.data['Car.ax'],
    'k--',
    name='long accel (sim)')
plt3.x_axis.link_to(plt2.x_axis)
plt3.x_axis.set_label('Time', units='s')
plt3.x_axis.enable_grid(True)
plt3.y_axis.set_label('Acceleration', units='m/s^2')
plt3.y_axis.enable_grid(True)